In [166]:
import numpy as np
import re
from tqdm import tqdm_notebook as tqdm
from sklearn import linear_model
from pymystem3 import Mystem
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer

In [148]:
with open('texts_train.txt', 'r') as file_texts:
    texts = np.array(file_texts.read().strip("\n").split("\n"))
file_texts.close()

with open('scores_train.txt', 'r') as file_scores:
    scores_str = np.array(file_scores.read().strip("\n").split("\n"))
    scores = np.array([int(elem) for elem in scores_str if elem != ''])
file_scores.close()

In [13]:
print("Mean score is", scores.mean())

Mean score is 7.8584


In [240]:
with open('dataset_40757_1 (22).txt', 'r') as file_tests:
    texts_test = file_tests.read().strip("\n").split("\n")
file_tests.close()

In [108]:
def maybe_to_lower(text):
    match = re.search("\w+", text)
    if not match:
        return text
    if text.isupper():
        return text
    return text.lower()

def tokenize(text):
    res = []
    ind = 0
    cur_seq = ""
    if_word = True
    
    n = len(text)
    stop_signs = set(['.', ',', '-', ';'])
    
    while True:
        if ind >= n:
           break 
        
        match = re.search("\w", text[ind])
        
        if if_word:
            if match:
                cur_seq += text[ind]
                ind += 1
            else:
                cur_seq = cur_seq.replace(' ', '')
                if cur_seq != '' and cur_seq not in stop_signs:
                    res.append(maybe_to_lower(cur_seq))
                cur_seq = text[ind]
                if_word = False
                ind += 1
        else:
            if match:
                cur_seq = cur_seq.replace(' ', '')
                if cur_seq != '' and cur_seq not in stop_signs:
                    res.append(maybe_to_lower(cur_seq))
                cur_seq = text[ind]
                if_word = True
                ind += 1
            else:
                cur_seq += text[ind]
                ind += 1
            
    return res
            
        
tokenize(texts[0])

['сериал',
 'очень',
 'люблю',
 'но',
 'академия',
 'и',
 'земля',
 'вызывает',
 'у',
 'меня',
 'отторжение',
 'идеей',
 '...',
 'не',
 'люблю',
 'когда',
 'принижают',
 'ценность',
 'человека',
 'как',
 'личности',
 'даже',
 'не',
 'смотря',
 'на',
 'ошибки',
 'личности']

In [150]:
tokenized_texts = []

for text in tqdm(texts):
    tokenized_texts.append(tokenize(text))

In [151]:
tokenized_texts[:10]

[['сериал',
  'очень',
  'люблю',
  'но',
  'академия',
  'и',
  'земля',
  'вызывает',
  'у',
  'меня',
  'отторжение',
  'идеей',
  '...',
  'не',
  'люблю',
  'когда',
  'принижают',
  'ценность',
  'человека',
  'как',
  'личности',
  'даже',
  'не',
  'смотря',
  'на',
  'ошибки',
  'личности'],
 ['думал',
  'что',
  'будет',
  'лучше',
  'идея',
  'очень',
  'интересна',
  'города',
  'иные',
  '..',
  'но',
  'в',
  'целом',
  'чуть',
  'выше',
  'чем'],
 ['с',
  'творчеством',
  'головачева',
  'я',
  'познакомился',
  'посредством',
  'этой',
  'книги',
  'понравилось',
  'дико',
  'и',
  'потом',
  'было',
  'жалко',
  'что',
  'остальные',
  'произведения',
  'подобного',
  'жанра',
  'ни',
  'по',
  'накалу',
  'страстей',
  'ни',
  'по',
  'сюжету',
  'даже',
  'блиско',
  'не',
  'подходили',
  'посланник',
  'мне',
  'вообще',
  'больше',
  'всех',
  'книг',
  'понравился',
  'у',
  'головачева'],
 ['то',
  'то',
  'я',
  'и',
  'в',
  'большое',
  'неудовольствие',
  'п

In [152]:
word2scores = {}

num_texts = len(texts)
num_scores = len(scores)

print(num_texts, num_scores)

for i in tqdm(range(num_texts)):
    tokenized = tokenized_texts[i]
    tokens_set = set(tokenized)
    score = scores[i]
    
    for token in tokens_set:
        if token not in word2scores:
            word2scores[token] = []
        word2scores[token].append(score)

20000 20000


In [153]:
word2scores.keys()

dict_keys(['вызывает', 'смотря', 'люблю', 'сериал', 'не', 'и', 'у', '...', 'отторжение', 'как', 'когда', 'но', 'ценность', 'на', 'принижают', 'ошибки', 'очень', 'даже', 'академия', 'личности', 'идеей', 'меня', 'земля', 'человека', 'города', 'чем', '..', 'интересна', 'иные', 'идея', 'в', 'будет', 'что', 'чуть', 'лучше', 'думал', 'целом', 'выше', 'страстей', 'подходили', 'всех', 'жалко', 'остальные', 'этой', 'жанра', 'посредством', 'посланник', 'было', 'сюжету', 'по', 'понравился', 'познакомился', 'блиско', 'головачева', 'книг', 'мне', 'подобного', 'дико', 'я', 'накалу', 'понравилось', 'ни', 'творчеством', 'больше', 'произведения', 'потом', 'вообще', 'книги', 'с', 'почему', 'артура', 'асприновский', '"..', 'стиль', 'неудовольствие', 'понимаю', 'теперь', 'прочитал', 'то', 'большое', '"', 'впечатлениям', 'только', 'дотягивает', 'смахивает', 'от', 'второпях', 'почитать', '(', 'такое', 'писалась', 'посланника', 'общим', 'местами', 'треть', 'вобщем', 'нечего', 'можно', ')', 'показалось', 'сил

In [155]:
word2score = {elem : np.array(word2scores[elem]).mean() for elem in word2scores.keys()}

In [65]:
word2score.keys()

dict_keys(['вызывает', 'смотря', 'люблю', 'сериал', 'не', 'и', 'у', '...', 'отторжение', 'как', 'когда', 'но', 'ценность', 'на', 'принижают', 'ошибки', 'очень', 'даже', 'академия', 'личности', 'идеей', 'меня', 'земля', 'человека', 'города', 'чем', '..', 'интересна', 'иные', 'идея', 'в', 'будет', 'что', 'чуть', 'лучше', 'думал', 'целом', 'выше', 'страстей', 'подходили', 'всех', 'жалко', 'остальные', 'этой', 'жанра', 'посредством', 'посланник', 'было', 'сюжету', 'по', 'понравился', 'познакомился', 'блиско', 'головачева', 'книг', 'мне', 'подобного', 'дико', 'я', 'накалу', 'понравилось', 'ни', 'творчеством', 'больше', 'произведения', 'потом', 'вообще', 'книги', 'с', 'почему', 'артура', 'асприновский', '"..', 'стиль', 'неудовольствие', 'понимаю', 'теперь', 'прочитал', 'то', 'большое', '"', 'впечатлениям', 'только', 'дотягивает', 'смахивает', 'от', 'второпях', 'почитать', '(', 'такое', 'писалась', 'посланника', 'общим', 'местами', 'треть', 'вобщем', 'нечего', 'можно', ')', 'показалось', 'сил

In [156]:
word2score[':(']

6.071428571428571

In [96]:
res_file = open("res.txt", "w")
res = ""

for text in texts_test:
    tokenized = tokenize(text)
    text_scores = np.array([word2score[elem] for elem in tokenized if elem in word2score])
    print(text_scores)
    if len(text_scores) == 0:
        res += "8\n"
    else:
        res += str(int(round(text_scores.mean()))) + "\n"
    
res_file.write(res)
res_file.close()

[7.66705363 8.29284526 7.76142433 8.03001876 8.58436214 7.70633894
 7.82758621 7.54077253 7.54945055 8.4        8.87544484 7.45880777
 7.78401728 7.40283688 7.97802198 7.4695836  7.50537634 7.75924412
 7.1270903  8.20385488 7.09090909 7.54945055 7.83700863 7.11111111
 9.         7.46100978 6.85245902 7.28135314 5.5        6.72264631
 6.66298343 7.         6.66298343 6.66298343 6.66298343]
[ 7.37160853  8.06666667 10.        ]
[8.07407407 7.82246016 8.37460064]
[7.08252427 7.62938426 4.         7.55555556 7.75924412 7.55873295
 8.1        7.14555964 1.66666667 7.4        7.44713776 8.
 7.54000804 5.5        7.76142433 5.83333333 9.         7.52608048
 6.         9.10465116 7.52173913 7.50537634 7.54000804 8.6
 8.         7.75924412 7.         8.3        7.83823529 6.03703704
 7.48399856 7.57385536 7.38754098 8.21428571 7.69318723 8.
 7.54000804 7.37029502 7.75924412 6.94642857 7.83627907 7.75924412
 9.         7.47586207 7.3        7.06666667 7.14859438 7.76142433
 7.04906542 6.        

 8.43529412 7.08333333 7.69318723 7.82352941 7.        ]
[7.38181818 7.5465587  7.05555556 8.20385488 7.36458333 7.57385536
 7.37796912 7.21822358 7.8410596  8.66666667 7.70633894 7.69318723
 8.03703704 8.57142857 6.58       4.         6.65909091 7.69002123
 7.22641509 8.20385488 7.81818182 6.83229814 7.57385536 7.3226942
 8.55882353 7.57385536 7.3226942  7.         7.66705363 6.96176471
 7.56470588 7.50144928 7.74509804 7.38527215 7.35504202 6.925
 7.21822358 7.99224806 7.57385536 7.69318723 7.83627907 7.54945055
 7.43718593 7.41082803 7.57385536 7.3226942  8.53658537 7.44067797
 7.14857143 8.14285714]
[7.45454545 8.37574967 7.37160853 7.04268293 7.66258503 7.4695836
 7.41118012 7.35504202 7.94339623 7.5        7.75924412 7.2
 7.75924412 7.69230769 7.42284569 7.36363636 7.5358235  7.3226942
 7.60270815 6.         7.75924412 7.08053691 7.44713776 8.02777778]
[7.28571429 7.15636364 7.57385536 7.46078431 8.20385488 7.84586466
 7.57385536 9.         7.60270815 7.35948905 7.08641975 7.4471

[ 6.68571429  7.          6.80952381  6.98        7.48399856  7.23770492
  8.37574967  7.4         8.          7.66705363  7.52941176  7.5358235
  7.65740741  7.54945055  6.61764706  7.         10.          7.35338346
  9.          6.69207317  7.74362819  5.28571429  9.          7.25575658
  6.875       6.90980392  7.6         7.82352941  6.1         6.875
  6.83333333  7.46590909  7.03055229  7.0625      7.2         6.5625
  5.89473684  7.25575658  8.          6.90980392  7.03055229  7.38527215
  7.51470588  7.4         8.          7.41939252  7.07407407  7.69318723
  8.14285714  7.75924412  7.5358235   6.06666667  7.42857143  6.83333333
  7.93333333  7.26315789  7.13157895  7.25        7.76142433  8.
  6.8125      7.75924412  7.3         7.44411765  6.8125      7.42284569
  7.76142433  8.          5.          6.94680851  7.66563945  7.49494949
  8.          7.69318723  6.35897436  6.64084507  7.760199    8.25
  7.          7.44713776  7.69318723  9.66666667  6.          7.09337349
  

[7.57385536 7.56470588 7.88245033 7.78934506 7.68888889 7.82246016
 7.36842105 7.21822358 7.46590909 7.34782609 7.30246914 6.74468085
 7.7173913  7.42502818 7.74468085 7.57385536 7.37029502 8.20385488
 7.63239875 7.4695836  7.60270815 7.35948905 6.90909091 7.22249389
 7.30246914 8.20385488 7.66258503 7.75924412 7.65681234 6.97615708
 8.37777778 7.45880777 7.54945055 7.57385536 8.37460064 7.37055838
 7.44067797 7.22187982 7.50537634 7.11317254 4.75       7.75924412
 7.78934506 7.68888889 5.5        8.         7.44713776 7.11784512
 6.41747573 7.62135922 7.53864734 6.92857143 6.96666667 7.76142433
 7.28571429 7.59183673 7.54385965 7.82608696 7.046875   7.78424015
 8.         7.74896552 7.22709163 7.42335766 7.75924412 7.5
 7.66705363 7.42335766 6.64912281 7.21822358 7.80752212 7.5
 7.54945055 7.38698011 8.37777778 7.49162011 7.65681234 7.21996753
 7.57587549 6.66666667 7.65       7.71035333 7.44713776 7.51114923
 8.         6.82782609 7.54000804 7.41666667 7.3226942  7.41463415
 6.527777

[7.6        7.54000804 8.         7.44713776 7.86394558 8.66666667
 6.35632184 7.04385965 8.53333333 7.44411765 8.66666667]
[8.7009901  7.68253968 8.54212454 7.64285714 7.39941691 7.15646259
 7.3810219  7.75924412 8.13345521 8.08795411 7.42171518 7.75924412
 7.94736842 7.72512011 7.75924412 7.5358235  7.28571429 9.
 7.6        8.20385488 3.         7.75924412 8.20385488 7.44067797
 7.4695836  6.75       7.44713776 7.69318723 7.44482366 7.57385536
 5.8        7.24175824 7.37699845 7.13513514 7.67741935 7.66666667
 7.34958678 7.5358235  7.67924528 6.76       7.25       7.22290389
 7.52608048 7.44713776 6.84285714 7.47733217 7.57563025 5.
 6.875      7.         7.52054795 6.5        7.61461794 8.11494253
 6.91549296 7.5        5.         7.46100978 7.46100978 9.66666667
 7.72512011 7.03846154 7.42502818 7.47733217 8.03164557 7.76142433
 7.60421546 7.89189189 7.5358235  7.75924412 7.69318723 7.01219512
 7.28409091 7.57417103 8.34782609 7.07575758 7.4695836  7.75924412
 7.57385536 7.4481409

...

[ 7.75        7.31044776  7.77477477  7.58947368  7.25575658  6.
  7.21822358  7.75924412  7.58947368  7.25575658  9.          6.9986413
  7.86258278  7.75        9.03225806  8.71428571  7.59429477  7.66559486
  7.40474906  7.88245033  7.69318723  8.20535714  7.12068966  7.
  7.40997706  7.25575658  7.71978022  7.13815789  8.125       7.17910448
  7.42682927  7.66666667  7.71035333  8.          7.55128205  7.76142433
  6.61616162  7.06065858  7.97239057  7.55128205  6.81818182  6.9986413
  7.54945055  7.67654321  7.19325153  6.15384615  7.53979239  7.54583333
  7.70633894  6.90740741  7.15909091  7.29274005  7.30909091  7.75924412
  7.57385536  7.48979592  7.08064516  7.47733217  7.06065858  7.25575658
  6.85        6.7         6.23214286  7.66705363  7.3810219   7.56859921
  7.04906542  7.5358235   7.33333333  7.56859921  5.          7.03055229
  8.20385488  7.19806452  8.19907407  7.65681234  7.69318723  9.
  7.75924412  7.54945055  7.67654321  7.19325153  7.69318723  7.44444444
  7.

[ 7.760199    9.31538462  7.25        7.75924412  7.13304253  7.86666667
  8.37460064  7.21996753  8.05504587  7.54945055  6.25        7.14555964
  7.          7.33076923  7.49606299  6.90829694  7.37699845  7.60270815
  7.44067797  6.96666667  7.71980676  7.14555964  6.78688525  6.83636364
  7.45880777  6.75        7.45880777  5.33333333  6.71428571  8.05376344
  7.70633894  7.77827248  7.5         7.45880777  7.75924412  7.40997706
  7.45880777  7.          5.5         8.5         7.          7.14555964
  7.58333333  8.16        7.62580645  7.70633894  9.          7.65237846
  7.33333333  7.82142857  7.97058824  6.90909091  7.72512011  7.4695836
  7.21996753  7.57385536  7.3226942   7.44713776  7.70930233  6.32173913
  7.75        7.21996753  7.33076923  7.55873295  7.44713776  7.70930233
  7.          7.96153846  8.37460064  7.3559322   7.3011583   8.37574967
  7.23770492  7.46100978  7.33076923  7.46100978  7.78934506  7.19806452
  6.60526316  7.625       6.69672131  7.75924412  7.

[8.20385488 8.23127036 7.97844828 8.34759358 7.4159292  7.54000804
 7.49446494 6.90131579 8.20385488 8.09108911 8.33944954 7.14555964
 5.8        7.75924412 8.125      7.4695836  7.60270815 7.3810219
 7.22818792 7.4180791  7.44713776 3.         7.65734266 7.75924412
 6.57894737 7.31730769 7.60270815 7.47733217 7.57563025 6.
 7.22290389 7.59574468 7.55555556 9.5        7.75924412 6.16666667
 6.6875     8.37574967 7.62938426 8.         6.77777778 7.75924412
 8.         7.675     ]
[]
[ 7.20923077  7.92207186  6.7625      7.47733217  7.76972281  7.57385536
  7.3226942   5.98181818  7.72512011  7.63636364  6.86792453  7.22222222
  7.75924412  8.04411765  7.52652259  7.75924412 10.          7.37160853
  7.12052731  7.3226942   7.57512953  6.71428571  7.46100978  7.44713776
  7.47733217  8.05376344  7.2173913   7.08721506  8.28571429  7.70588235
  7.36       10.          7.54945055  8.15007899  7.48406139  8.
  7.40384615  7.44713776  7.29411765  8.03571429  7.24210526  6.97674419
  7.540008

 7.3226942  7.12068966 7.38095238 7.8440367  7.44713776]
[6.13793103 6.17857143 6.90298507 7.54000804 7.38527215 7.57385536
 7.0625     6.63636364 7.75924412 6.83333333 7.2        7.7721519
 7.51698514 7.57385536 7.0625     6.63636364 7.75924412 6.83333333
 7.2        7.4481409  7.75       7.2446675  7.44713776 6.6
 7.00817996 6.33333333 5.         7.75924412 7.36512027 6.359375
 6.43589744 5.85714286 5.         7.54945055 6.94444444 7.75924412
 7.36512027 7.57385536 5.66666667 6.43939394 5.33333333 7.37160853
 7.46100978 7.44713776 7.31818182]
[ 8.19907407  7.95121951  7.03278689  7.75        7.97844828  7.30769231
  7.50909091  7.45880777  7.5358235   7.28888889  7.75924412  6.02666667
  9.          7.35483871  7.48399856  7.75924412  8.14285714  7.75924412
  8.66666667  6.          7.37796912  7.66666667  7.75924412  7.
  8.05769231  7.46100978  7.3559322   7.08721506  7.          7.44067797
  6.95652174  7.304       7.13304253  6.92857143  7.54000804  7.77777778
  8.          7.647

  7.69318723  7.47797357]
[8.4272     7.75924412 7.7173913  9.         2.         7.44067797]
[ 7.31818182  7.82246016  8.20385488  7.68047337  7.41463415  7.4200627
  7.60270815  6.8         7.86258278  6.41666667  7.4         2.5
  7.74358974  7.4695836   7.50649351  7.55873295  6.21052632  5.
  7.70633894  4.875       7.44713776  6.86046512  6.61403509  6.11111111
  8.08571429  7.46100978  7.5358235   8.55813953  7.48995984  7.54000804
  7.37029502  7.92857143  7.37029502  7.33333333  7.31940299  8.46241458
  7.46100978  7.03225806  7.46100978  7.76142433  8.08888889  7.46100978
  7.22222222  7.08721506  7.5358235   6.62162162  7.37160853  6.98138748
  7.33076923  7.46100978  7.61111111  7.46100978  7.56239016  7.60270815
  7.54945055  7.35855263  7.29032258  7.40997706  6.64285714 10.
  7.5358235   7.55873295  7.44713776  7.03984064  7.33333333  6.9375
  7.8         7.73684211  7.25474255  8.          6.          7.3641791
  7.44713776  7.77777778  7.716       8.5         7.8224601

In [117]:
def tokenize_to_words(text):
    words = re.split("\W+", text)
    res = [elem.lower() for elem in words if elem != '']
    return res
        
tokenize_to_words(texts[0])

['сериал',
 'очень',
 'люблю',
 'но',
 'академия',
 'и',
 'земля',
 'вызывает',
 'у',
 'меня',
 'отторжение',
 'идеей',
 'не',
 'люблю',
 'когда',
 'принижают',
 'ценность',
 'человека',
 'как',
 'личности',
 'даже',
 'не',
 'смотря',
 'на',
 'ошибки',
 'личности']

In [118]:
word2scores = {}

num_texts = len(texts)
num_scores = len(scores)

print(num_texts, num_scores)

for i in tqdm(range(num_texts)):
    tokenized = tokenized_texts[i]
    tokens_set = set(tokenized)
    score = scores[i]
    
    for token in tokens_set:
        if token not in word2scores:
            word2scores[token] = []
        word2scores[token].append(score)
        
word2score = {elem : np.array(word2scores[elem]).mean() for elem in word2scores.keys()}

20000 20000


In [121]:
res_file = open("res.txt", "w")
res = ""

for text in texts_test:
    tokenized = tokenize(text)
    text_scores = np.array([word2score[elem] for elem in tokenized if elem in word2score])
    print(text_scores)
    if len(text_scores) == 0:
        res += "8\n"
    else:
        res += str(int(round(text_scores.mean()))) + "\n"
    
res_file.write(res)
res_file.close()

[7.71135293 7.77291886 7.54993342 7.4084507  8.17231125 7.39311099
 7.44212753 7.56323417 7.39469697 7.77291886 7.47088321 7.22244898
 8.66666667 7.77291886 6.         6.78025478 7.39419087 7.79939668
 7.54993342 7.77291886 7.54993342 7.44673502 7.59339975 7.47088321
 7.98156682 7.73890785 7.17333333 7.59339975 7.625      7.77291886
 8.09090909 7.64920104]
[ 7.2713712   7.77291886  7.37037037  7.54993342  7.56323417  7.61226994
  7.39469697  7.62721     7.24475524  7.56323417  7.44444444 10.
 10.          7.77291886  7.4200627   7.69618451  6.859375  ]
[ 7.55        7.39469697  7.77291886  7.14652956  7.56323417  7.62721
  7.44673502  7.30566219  7.69230769  7.72264281  7.62721     7.59006211
  8.17231125  7.64920104  7.13304253  7.56323417  6.97589099  7.54993342
  7.37037037  7.48648649  7.07462687  7.37037037  7.71135293  7.76237037
  6.5         7.48648649  7.62721     7.61248852  9.          7.95454545
  7.24475524  7.56323417  7.55572636  7.07462687  8.2         7.07462687
  7.44

 7.01441153 6.35869565]
[ 7.37037037  7.91948172  7.44673502  7.56859921  7.78571429  7.53715406
  7.21690141  7.28520499  7.53775122 10.          7.07462687  7.92307692
  6.97589099  6.55        6.97589099  7.10365854  6.9787234   7.38562409
  6.5         7.37037037  7.53312303  7.45762712  7.          7.47107438
  8.          7.72307692  8.06126126  6.83333333  7.77291886  7.52018531
  7.20833333  7.91948172  7.47494631  7.77291886  7.5         7.71135293
  9.          6.9         7.40636042  7.41666667  7.47088321  7.52608048
  7.56323417  7.44673502  7.67728694  7.41666667  8.03243243  7.47352298
  7.23076923  7.23387097  7.76237037  7.91948172  7.62721     7.55748663
  7.8277027   7.77291886  7.4494382   7.11070111  7.07423581  7.56859921
  7.37037037  7.11317254  7.47088321  7.69326395  7.36429872  7.56859921
  7.40636042  7.42708333  7.48221344  7.44744568  7.          7.69556025
  7.40449438  6.98885794  7.44673502  7.73356064  7.33049404]
[8.20072007 5.41818182 7.77291886 7.44

 7.56859921 7.71135293 7.56859921]
[ 7.3038674   7.36429872  6.86524823  7.77291886  8.22264151  7.96774194
  7.47733217  5.5         7.77291886  7.44744568  7.35294118  7.07462687
  7.64920104  6.32298137  8.          7.01923077  6.          7.77291886
  7.20967742  7.18292683  7.25        8.          7.07462687  7.07462687
  7.07462687  7.77291886  7.07462687  6.74468085  7.07462687  7.29411765
  7.85714286  7.43009321  7.54993342  7.55572636  7.17333333  7.34958678
  7.47733217  7.44744568  8.5         7.48584906  7.36862409  7.07462687
  7.35294118  7.07462687  7.38859764  7.00203666  7.44673502  7.09090909
  7.50444727  7.71387697  7.2         7.64920104  7.47733217 10.
  7.77291886  8.26420233  8.46995708  7.1826087   7.42857143  7.47733217
  8.89230769  7.07462687  6.17391304  7.81113281  7.07462687  7.54993342
  7.7114925   7.97694175  7.40062354  7.48584906  6.82608696  7.77291886
  8.20072007  8.20072007  6.83333333  6.71428571  7.37918599  7.40449438
  7.51400329  7.71135293

 7.50444727 7.44673502 7.71135293]
[7.2184466  7.07137907 7.39469697 7.125      7.64920104 7.55
 7.62721    7.49456522 7.13304253 7.77291886 7.79674797 7.71135293
 7.125      6.36065574 7.44673502 7.64920104 7.55       7.56323417
 6.9        7.71135293 7.44212753 7.5625     7.22875817 7.59339975
 7.         7.22875817 7.77291886 7.56323417 7.         7.125
 7.64920104 7.55       7.38562409 7.77291886 7.56323417 7.32796661
 7.41315136 7.47107438 7.40209268 7.125      7.77291886 6.8255814
 7.49275362 7.71135293 7.55       6.8255814  7.38562409 6.5
 6.         7.76237037 7.53595997 2.         7.23287671 2.
 7.36862409 7.61579297 7.52018531 7.71135293 7.43309859 7.77291886
 7.0625     7.53715406 7.38562409 7.69326395 7.36429872 7.91680815
 7.71135293 7.61579297 7.38562409 7.44673502 7.44673502 7.77291886
 7.22222222 7.56323417 7.44444444 7.30434783 8.20072007 8.13693694
 7.84644195]
[7.44673502 7.77291886 7.72828784 7.01941748 4.78735632]
[ 7.30566219  7.76237037  7.36862409  7.44673502  7

 7.57096774 7.72264281 7.47352298 7.67728694 6.83333333 7.48845471]
[8.12564103 6.88888889 7.35986159 7.45059289 7.77291886 7.44212753
 7.44673502 7.71135293 7.44744568 7.44673502 7.44212753]
[5.46808511 7.44744568]
[7.40449438 7.48809524 7.47107438 7.54993342 8.         7.56323417
 7.71135293 6.7962963  7.20233463 7.53312303 7.77291886 6.4
 6.9        7.72828784 7.54993342 7.62721    7.61226994 7.36862409
 7.20233463 6.58333333 7.53312303 7.56323417 7.71135293 7.84782609
 7.31515152 7.2184466  7.38888889 7.77291886 7.60546875 7.77291886
 7.81113281 7.44673502 7.64920104 7.74477612 7.72828784 7.98156682]
[8.17231125 8.03243243 7.38859764 7.36862409 7.74477612 7.07462687
 8.91666667 8.06666667 7.47088321 7.00203666 7.44673502 6.89189189
 7.37037037 7.47088321 7.44212753 7.01612903 7.81818182 8.17231125]
[7.91948172 8.17231125 8.26420233 7.15151515 5.        ]
[7.16082225 7.91240876 7.97694175 7.71135293 7.70979021 7.38562409
 7.97694175 7.54993342 7.47088321 7.81113281 7.39469697 7.3686

  7.34958678  7.33049404]
[7.76274945 3.         7.41146132 6.36842105 8.5        8.5
 7.37918599 8.21875    7.55837563 7.44212753 7.07894737 9.
 7.54993342 7.19047619 7.75       7.76237037]
[8.17231125 7.40062354 8.         7.47744361 5.03333333 7.71135293
 7.76237037 7.71135293 7.18181818 6.4        8.20072007 8.36263736
 7.55572636 7.64920104 7.21690141 7.33049404 7.5960452  7.41666667
 7.77291886 7.41666667 7.55572636 7.42171518 7.44744568 8.20072007
 7.77291886 8.20072007 7.29450549 6.90829694 7.07462687 7.07462687
 7.3253012  7.71387697 7.47494631 7.53715406 7.50444727 8.
 5.66666667 7.37918599 7.54993342 7.48905109 7.77291886 7.53715406
 7.44212753 6.80991736 7.54993342 7.48584906 7.76190476 7.44673502
 6.80991736 7.07137907 7.39469697 7.50444727 7.56323417 7.71135293
 7.24699454 7.40366972 7.71135293 6.         6.64       7.71135293
 6.83333333 7.77291886 7.25       7.40062354 7.42857143 7.55572636
 7.48584906 6.97589099 7.9206623  7.40449438 7.44673502 6.80991736
 7.62721    6

 7.0306834  7.33049404]
[7.98156682 7.425      7.54489682 7.97694175 7.44744568 7.77291886
 7.71135293 7.59461599 7.77291886 6.5        7.61261261 7.38562409
 7.48933527 7.09375    7.44673502 7.44744568 7.54993342 8.13606655
 7.79939668 7.69078947 7.48809524 8.09708738 7.77777778 7.36862409
 7.5        7.77291886 7.36862409 7.6852116  7.41127349 7.6678618
 7.50444727 7.41146132 7.44673502 9.         7.35974304 7.15730337
 8.42886179 7.77291886 7.7        7.02040816 7.42656326]
[7.89308176 7.53715406 7.00203666 7.78571429 7.71135293 7.34958678
 7.34958678 7.34958678 7.07462687 7.53715406 7.50444727 7.73076923
 7.77291886 7.07423581 8.5        7.39311099 7.74477612 7.00203666
 7.44673502 7.48355263 7.77291886 7.57777778 7.01242236 7.47352298
 7.18181818 7.47088321 7.56323417 5.7        7.64748201 7.54993342
 7.05128205 7.77291886 7.89308176 7.4373928  7.44673502 7.45098039
 7.82051282 7.11317254 7.56196841 7.59461599 7.56323417 7.62721
 7.07462687 6.92307692 4.78735632 7.54993342 7.37918

 7.82442068 7.77291886 8.1650165 ]
[4.66666667 7.44673502 7.40449438 7.55572636 7.81113281 7.44673502
 7.77291886 7.07462687 3.         7.07462687 7.76237037 6.7107438
 5.71428571 7.44106667 6.33333333 7.4691358  7.89308176]
[7.44673502 7.42656326 9.         7.30566219 7.56859921 7.78846154
 7.56323417 7.39469697 7.07462687 8.03243243 7.71135293 7.07462687
 7.77291886 7.1344086  6.97794118 7.38562409 6.78938053 7.56196841
 7.77291886 4.         7.45059289 7.47352298 7.56859921 9.
 7.45059289 7.4494382  7.12268908]
[7.2        7.55572636 7.56323417 7.77565632 7.22290389 6.77777778
 5.71428571 7.54032258 7.01441153]
[7.44673502 7.53595997 7.62721    7.44744568 6.5        7.41146132
 7.33049404 7.22290389 7.17475728]
[7.07462687 7.47352298 7.71135293 7.56196841 7.59339975 7.44673502
 7.34642857 7.72828784 7.47352298 7.59339975 7.07462687 7.16082225
 7.91948172 7.22290389 5.        ]
[7.32348993 7.77291886 7.15384615 7.53312303 7.39311099 8.20072007
 7.66492147 7.69326395 7.77291886 7.7113

In [157]:
mystem = Mystem()

In [158]:
tokenized_texts = []

for text in tqdm(texts):
    tokenized = tokenize(text)
    text_ = " ".join(tokenized)
    lemmatized = mystem.lemmatize(text_)
    res = [elem for elem in lemmatized if elem != ' ' and elem != '\n']
    tokenized_texts.append(res)

tokenized_texts[:10]

[['сериал',
  'очень',
  'любить',
  'но',
  'академия',
  'и',
  'земля',
  'вызывать',
  'у',
  'я',
  'отторжение',
  'идея',
  '...',
  'не',
  'любить',
  'когда',
  'принижать',
  'ценность',
  'человек',
  'как',
  'личность',
  'даже',
  'не',
  'смотря',
  'на',
  'ошибка',
  'личность'],
 ['думать',
  'что',
  'быть',
  'хорошо',
  'идея',
  'очень',
  'интересный',
  'город',
  'иной',
  '..',
  'но',
  'в',
  'целое',
  'чуть',
  'высоко',
  'что'],
 ['с',
  'творчество',
  'головачев',
  'я',
  'познакомиться',
  'посредством',
  'этот',
  'книга',
  'понравиться',
  'дико',
  'и',
  'потом',
  'быть',
  'жалко',
  'что',
  'остальной',
  'произведение',
  'подобный',
  'жанр',
  'ни',
  'по',
  'накал',
  'страсть',
  'ни',
  'по',
  'сюжет',
  'даже',
  'блиско',
  'не',
  'подходить',
  'посланник',
  'я',
  'вообще',
  'много',
  'все',
  'книга',
  'понравиться',
  'у',
  'головачев'],
 ['то',
  'то',
  'я',
  'и',
  'в',
  'большой',
  'неудовольствие',
  'прочитыват

In [126]:
word2scores = {}

num_texts = len(texts)
num_scores = len(scores)

print(num_texts, num_scores)

for i in tqdm(range(num_texts)):
    tokenized = tokenized_texts[i]
    tokens_set = set(tokenized)
    score = scores[i]
    
    for token in tokens_set:
        if token not in word2scores:
            word2scores[token] = []
        word2scores[token].append(score)

20000 20000


In [146]:
res_file = open("res.txt", "w")
res = ""

for text in texts_test:
    tokenized = tokenize(text)
    text_ = " ".join(tokenized)
    lemmatized = mystem.lemmatize(text_)
    result = [elem for elem in lemmatized if elem != ' ']
    
    text_scores = np.array([word2score[elem] for elem in result if elem in word2score])
    #print(text_scores)
    if len(text_scores) == 0:
        res += "8\n"
    else:
        res += str(int(round(text_scores.mean()))) + "\n"
    
print(res)
res_file.write(res)
res_file.close()

8
7
7
8
8
8
7
8
8
7
8
8
8
8
8
8
8
7
8
7
7
8
7
8
7
8
8
7
8
7
7
8
7
7
7
7
8
8
8
8
7
7
8
7
8
8
8
8
8
8
7
8
8
7
8
7
7
8
7
7
8
8
7
8
8
8
7
7
8
7
7
8
7
8
8
7
7
7
7
7
8
8
8
7
8
7
7
7
7
8
8
8
8
8
7
8
8
8
7
7
8
8
7
8
8
7
7
8
8
7
8
8
8
7
7
8
8
8
8
8
8
8
7
8
8
8
7
7
7
8
8
8
8
8
8
7
7
8
7
8
8
8
8
8
7
8
7
8
7
8
8
8
7
8
7
8
7
8
7
8
8
7
7
8
8
7
8
8
7
7
8
8
8
8
8
8
7
7
7
7
8
8
7
8
8
7
8
8
8
7
7
8
8
8
7
8
7
8
8
8
7
7
7
7
8
8
7
8
7
8
8
8
8
7
8
7
8
7
7
8
8
7
7
7
7
8
8
8
7
8
8
8
7
8
8
8
7
8
7
8
7
8
7
7
8
8
7
7
8
8
8
8
7
8
7
8
8
8
8
7
8
7
7
7
8
8
8
8
8
7
8
8
7
7
7
8
7
8
8
7
7
8
8
8
8
7
8
8
8
7
7
8
6
8
7
8
8
7
8
7
7
7
7
7
8
7
7
7
8
7
8
8
7
8
7
8
8
8
8
7
8
7
7
7
7
7
8
8
7
7
8
7
8
7
8
8
8
7
7
8
8
8
8
8
7
7
7
8
8
8
8
7
7
8
8
8
7
8
7
8
7
8
8
8
7
8
8
8
8
8
8
8
8
7
8
8
8
7
7
7
8
8
7
7
7
8
7
8
8
7
7
7
8
8
8
8
8
8
7
8
8
8
8
8
8
7
8
8
8
8
8
7
8
8
7
8
7
7
8
8
8
8
8
8
8
8
8
7
8
8
7
8
7
8
8
8
8
8
8
8
8
8
8
8
7
7
8
8
8
7
8
8
8
8
8
8
8
8
7
8
7
8
7
7
8
7
8
8
8
7
8
8
8
7
8
8
8
7
8
8
8
8
8
8
7
7
8
8
7
7
8
7
8
7
7
8
7
7
8
8


In [159]:
final_texts = [" ".join(elem) for elem in tokenized_texts]

In [160]:
final_texts[:10]

['сериал очень любить но академия и земля вызывать у я отторжение идея ... не любить когда принижать ценность человек как личность даже не смотря на ошибка личность',
 'думать что быть хорошо идея очень интересный город иной .. но в целое чуть высоко что',
 'с творчество головачев я познакомиться посредством этот книга понравиться дико и потом быть жалко что остальной произведение подобный жанр ни по накал страсть ни по сюжет даже блиско не подходить посланник я вообще много все книга понравиться у головачев',
 'то то я и в большой неудовольствие прочитывать  "  артур  " .. теперь понимать почему стиль на асприновский',
 'как я показываться место сильно смахивать на посланник но по общий впечатление не дотягивать концовка  (  последний треть книга  )  такой ощущение писаться второпях вобщий почитать можно только от нечего',
 'от первый часть книга просто отрываться не мочь уж больно захватывать быть похождение бывший афганец по древний русь от второй часть отрываться мочь но ненадолго'

In [162]:
test_dataset = []

for text in texts_test:
    tokenized = tokenize(text)
    text_ = " ".join(tokenized)
    lemmatized = mystem.lemmatize(text_)
    result = [elem for elem in lemmatized if elem != ' ']
    result = " ".join(result)
    test_dataset.append(result)

In [163]:
test_dataset[:10]

['(  29  /  12  /  07  )  легко и непринужденный правда признаваться книга я не читать .. я она слушать  ) . конец и правда разочаровывать но в общий очень понравиться ! не поклонник мурак но кой что из написать увлекать и подарить ощущение который на тот момент не находить у другой писатель хотя сейчас мочь выделять несколько ... читать переживать все в себя если книга действительно стоить внимание для конкретный личность то она и быть подобный переживать приключение если же нет книга просто не ваш \n',
 'потрясно !  я обожать этот книга \n',
 'да весь очень знакомый когда все раздражать хотеться близкий человек сделать назло больно это переходный возраст у ребенок а вот мать возможно действительно болезнь альцгеймер конец на мой взгляд немного недосказывать саундтрек просто супер \n',
 'созвучно \n',
 'книга о любовь реальный и виртуальный главный герой встречаться в аська страсть накаляться вот они уже собираться встречаться в реальный жизнь что же это заканчиваться ? ну без бурный 

In [199]:
vectorizer = CountVectorizer(binary=True, ngram_range=(2, 3))
train_dataset = vectorizer.fit_transform(final_texts)

model = linear_model.SGDClassifier().fit(train_dataset, scores)

res_file = open("res.txt", "w")
res = ""

for text in test_dataset:
    vectorized = vectorizer.transform([text])
    unclipped_res = int(round(model.predict(vectorized)[0]))
    
    res += str(np.clip(unclipped_res, 1, 10)) + "\n"

print(res)
res_file.write(res)
res_file.close()

10
10
7
8
10
8
8
10
6
8
5
7
4
9
10
9
7
6
10
8
8
10
8
10
8
10
9
3
10
9
5
10
6
5
10
8
10
10
10
10
9
10
10
10
7
8
10
9
10
10
4
10
10
10
9
9
10
9
9
9
10
10
8
3
10
10
9
8
10
9
9
3
10
8
8
9
4
9
10
9
9
8
8
9
8
10
8
7
8
10
10
10
9
10
9
9
10
8
7
9
8
8
9
10
6
10
9
9
7
10
9
10
10
10
10
6
8
5
10
3
8
9
10
10
10
6
10
10
10
9
9
10
10
9
9
9
8
7
9
10
10
10
7
10
8
8
5
10
2
10
9
10
10
10
9
9
9
7
3
10
9
8
5
5
9
10
9
9
8
9
10
9
9
4
10
5
8
5
8
10
10
9
9
9
9
10
9
7
8
10
9
9
10
9
10
9
10
9
6
8
9
8
10
10
8
9
10
9
10
10
9
10
10
8
10
9
10
6
7
10
6
9
8
10
9
10
8
2
10
9
9
10
10
10
8
10
6
9
5
7
10
9
10
8
10
9
9
8
10
9
10
10
10
10
5
9
10
5
7
10
9
8
10
8
10
10
10
10
10
9
10
10
10
9
9
10
8
8
6
6
9
10
8
10
8
10
10
10
8
10
8
8
10
6
10
10
4
8
10
9
8
9
9
9
10
10
10
8
10
8
10
9
4
5
10
7
10
7
9
10
7
9
10
8
10
9
9
10
10
7
9
9
10
7
10
10
9
10
8
10
9
9
9
9
8
7
9
10
10
10
10
6
10
5
10
7
10
9
10
10
10
10
10
5
10
10
9
9
10
8
8
7
9
8
10
5
10
10
9
9
10
10
7
10
4
9
9
10
9
9
9
10
9
5
10
10
10
10
10
9
10
7
8
10
9
9
9
7
9
8
9
10
10
8
1

In [211]:
vectorizer = CountVectorizer(binary=True, ngram_range=(1, 2))
train_dataset = vectorizer.fit_transform(final_texts)

model = linear_model.SGDRegressor().fit(train_dataset, scores)

res_file = open("res.txt", "w")
res = ""

for text in test_dataset:
    vectorized = vectorizer.transform([text])
    unclipped_res = int(round(model.predict(vectorized)[0]))
    
    res += str(np.clip(unclipped_res, 1, 10)) + "\n"

print(res)
res_file.write(res)
res_file.close()

10
6
8
6
7
9
5
6
7
8
7
8
9
9
7
10
10
2
10
7
7
10
9
7
9
9
7
10
10
8
10
10
7
6
9
8
10
7
7
4
6
7
9
10
9
9
9
7
10
9
10
9
7
8
6
7
7
6
5
7
5
6
10
8
8
10
8
8
8
10
10
6
8
7
5
8
8
7
9
8
9
7
8
6
7
10
6
7
7
6
7
9
6
7
6
8
10
9
8
6
8
7
6
10
5
5
8
6
6
8
8
8
7
6
7
6
9
10
10
6
10
6
8
7
4
7
5
7
6
7
6
8
10
8
8
4
7
5
10
7
10
7
9
6
7
8
5
6
6
8
6
10
3
7
10
10
8
3
8
6
7
8
6
7
10
9
7
6
10
8
10
8
8
9
4
9
6
7
5
2
7
10
5
9
10
10
8
6
6
10
5
8
5
6
10
10
7
4
10
10
7
8
10
8
10
4
6
6
5
6
8
9
8
5
7
5
8
10
7
6
7
8
6
6
6
10
10
6
10
7
7
9
6
6
7
8
6
7
7
5
8
10
8
9
9
10
10
9
5
10
9
10
9
6
9
4
8
7
5
5
8
5
8
10
9
6
6
7
4
7
8
6
8
7
10
10
10
6
10
10
7
10
10
9
10
1
2
8
10
6
10
8
7
4
10
7
8
2
7
8
8
8
6
9
7
8
9
6
9
9
8
9
7
6
9
9
10
7
6
1
8
8
8
9
5
9
9
9
3
7
10
5
8
6
9
4
8
9
6
8
10
8
10
10
7
10
9
6
7
10
10
6
6
9
8
8
10
5
3
8
8
9
9
5
9
10
8
5
8
9
9
10
8
9
7
10
9
10
8
7
9
9
7
10
3
7
7
10
5
7
7
10
10
8
8
6
7
8
7
10
7
6
4
1
10
10
7
6
10
4
8
6
7
4
7
9
9
5
10
5
9
10
5
8
7
10
8
6
9
7
10
9
7
7
6
10
8
10
6
8
9
5
10
8
6
10
7
9
9
6
8
9
8
7


In [236]:
vectorizer = TfidfVectorizer(ngram_range=(1, 3))
train_dataset = vectorizer.fit_transform(final_texts)

model = linear_model.PassiveAggressiveRegressor().fit(train_dataset, scores)

res_file = open("res.txt", "w")
res = ""

for text in test_dataset:
    vectorized = vectorizer.transform([text])
    unclipped_res = int(round(model.predict(vectorized)[0]))
    
    res += str(np.clip(unclipped_res, 1, 10)) + "\n"

print(res)
res_file.write(res)
res_file.close()

9
7
6
7
7
10
8
7
10
10
10
9
8
6
10
8
10
8
7
10
6
10
10
8
10
3
8
9
10
9
6
7
8
9
8
9
9
9
4
10
8
6
7
7
9
7
8
6
9
9
6
9
8
9
10
8
9
8
7
8
9
9
9
8
8
7
8
9
7
10
7
9
10
9
8
6
7
10
7
6
6
10
9
10
9
10
8
7
8
6
10
8
8
10
5
10
10
9
9
9
6
10
10
7
9
8
6
10
8
9
7
7
9
9
8
9
7
7
7
8
10
7
3
6
10
6
10
9
7
7
8
10
8
6
9
7
7
8
7
9
8
7
9
10
8
10
1
4
9
7
9
9
10
9
5
4
7
8
10
9
9
10
6
6
7
10
7
6
3
6
8
7
10
8
10
7
8
9
7
7
8
9
8
10
10
6
8
9
10
9
10
8
10
10
8
7
8
10
9
8
10
6
8
9
7
7
10
9
10
9
9
8
8
9
7
9
7
9
6
8
6
9
5
6
9
8
7
9
9
7
7
7
7
9
8
10
6
7
6
9
7
7
9
9
10
7
8
8
9
6
10
10
8
6
6
7
5
7
6
8
9
8
7
10
7
7
5
10
10
7
9
6
9
6
5
4
4
9
6
8
6
9
3
10
10
10
8
9
9
10
8
9
10
8
10
10
7
8
8
8
7
7
7
8
6
9
6
6
10
6
10
9
9
9
7
10
8
5
9
9
7
8
6
2
6
7
8
9
7
10
7
9
9
10
10
7
6
8
7
9
9
8
2
8
3
6
9
9
6
5
9
5
7
5
10
9
7
10
9
5
10
8
7
9
10
10
10
7
7
9
6
7
7
9
8
8
8
8
9
9
8
8
10
8
5
7
10
10
8
8
10
5
7
8
6
6
8
4
6
7
10
8
9
6
7
10
6
9
6
8
10
10
10
8
8
8
4
3
6
6
8
9
8
6
7
9
10
9
10
9
10
10
4
8
10
9
6
9
8
8
8
9
9
8
9
6
7
8
8
6
8
5
5
5
10
9

In [241]:
test_dataset = []

for text in texts_test:
    tokenized = tokenize(text)
    text_ = " ".join(tokenized)
    lemmatized = mystem.lemmatize(text_)
    result = [elem for elem in lemmatized if elem != ' ']
    result = " ".join(result)
    test_dataset.append(result)

In [242]:
vectorizer = TfidfVectorizer(ngram_range=(1, 3))
train_dataset = vectorizer.fit_transform(final_texts)

model = linear_model.SGDClassifier().fit(train_dataset, scores)

res_file = open("res.txt", "w")
res = ""

for text in test_dataset:
    vectorized = vectorizer.transform([text])
    unclipped_res = int(round(model.predict(vectorized)[0]))
    
    res += str(np.clip(unclipped_res, 1, 10)) + "\n"

print(res)
res_file.write(res)
res_file.close()

9
10
10
10
5
8
10
5
8
9
10
8
9
9
10
10
7
10
9
8
5
6
9
10
9
10
10
10
10
10
10
10
9
4
10
8
10
10
8
8
8
8
10
10
9
10
7
10
10
8
10
9
10
10
9
10
10
9
10
10
10
10
9
10
10
10
9
8
10
10
7
9
10
8
7
9
9
10
8
9
8
10
9
9
8
9
9
1
9
10
10
10
10
10
10
8
10
6
8
5
10
10
8
10
10
7
9
10
10
8
5
8
8
10
10
10
8
10
10
7
10
8
10
8
5
8
7
10
10
10
10
10
10
9
5
8
9
9
10
8
10
9
8
8
10
8
10
8
10
10
9
10
10
10
7
8
8
9
10
8
10
10
10
10
10
8
9
9
10
7
9
1
8
8
9
10
9
10
9
8
4
10
10
9
6
8
8
10
10
10
9
10
5
5
7
4
5
10
10
3
9
9
8
10
9
10
10
10
9
10
10
6
10
10
8
10
10
10
5
10
9
10
10
7
9
8
8
5
2
10
10
7
9
10
9
10
9
8
10
5
9
10
5
10
7
9
8
10
8
9
10
10
10
8
10
9
10
7
4
10
8
1
4
10
8
9
9
8
9
8
10
10
9
7
8
10
8
10
10
8
10
7
10
10
10
9
10
10
9
8
10
9
10
10
10
10
9
10
10
10
9
5
9
10
10
10
8
5
10
9
10
9
10
8
8
10
10
10
9
10
10
10
8
6
9
5
8
10
10
8
8
4
10
10
6
8
10
10
5
3
8
9
9
10
9
8
10
9
8
10
9
5
10
10
10
10
8
8
9
10
10
10
10
9
10
10
10
10
10
10
10
8
10
8
10
10
10
8
8
9
7
3
10
9
8
8
8
9
7
9
4
8
10
10
9
7
10
10
8
9
10
9
9
10
10
1

In [164]:
vectorizer = TfidfVectorizer(ngram_range=(1, 3))
train_dataset = vectorizer.fit_transform(final_texts)

model = linear_model.Ridge().fit(train_dataset, scores)

res_file = open("res.txt", "w")
res = ""

for text in test_dataset:
    vectorized = vectorizer.transform([text])
    unclipped_res = int(round(model.predict(vectorized)[0]))
    
    res += str(np.clip(unclipped_res, 1, 10)) + "\n"

print(res)
res_file.write(res)
res_file.close()